## Loading & Formatting Features

### Imports

In [1]:
# Loading 
from pathlib import Path
from os import path
import sys

# Custom library from WIPAR
import ci_lib
from ci_lib.utils import snakemake_tools
from ci_lib.features import Features, Means, Raws, Covariances, AutoCovariances, Moup, AutoCorrelations, Feature_Type
from ci_lib.plotting import graph_circle_plot, plot_glassbrain_bokeh, draw_neural_activity
from ci_lib import DecompData
from ci_lib.feature_selection import RFE_pipeline
from ci_lib.networks import construct_network, construct_network_from_feat, add_bokeh_attributes

# Processing
import numpy as np
import networkx as nx

# Dict Formating
import json     
import collections
import pandas as pd

# Plotting
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go


ModuleNotFoundError: No module named 'h5py'

In [67]:
#Helper functions
def print_dict_keys(print_dict):
    if type(print_dict) is dict:
        print(print_dict.keys())
        print_dict_keys(next(iter(print_dict.values())))
    else:
        print(f"example shape of feature {print_dict.shape}")


### Loading

In [68]:
feat_dict = np.load(Path.cwd()/"results/aggregated_feats.npy", allow_pickle=True)

print_dict_keys(feat_dict)

dict_keys(['GN06.2021-03-26_10-53-05', 'GN06.2021-03-29_11-51-27', 'GN06.2021-04-01_13-44-22', 'GN06.2021-03-01_13-57-39', 'GN06.2021-03-02_15-49-02', 'GN06.2021-03-03_14-02-06', 'GN06.2021-03-04_11-51-23', 'All'])
dict_keys(["anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,MOs-L,SSp-bfd-L,VISrl-L,VISp-L']", 'anatomical_ROI~[]'])
dict_keys(['All'])
dict_keys(['leftResponse_leftStim', 'leftResponse_rightStim', 'rightResponse_rightStim', 'rightResponse_leftStim', 'noResponse'])
dict_keys(['mean', 'autocovariance_timelags~[1]'])
example shape of feature (115, 8)


In [81]:
#Due to the generic nature of the pipeline, the loaded feature mirror the internal file structure resulting from the independent runs
#This structure is sessions x parcellation x selected_trials x conditions x features
#Here we transform them to
#Parcellation x Feature x Condition x  (Combined Sessions) + Session

feats = {}

for session,sdict in feat_dict.items():
    for parcellation,pdict in sdict.items():
        feats[parcellation]=feats.get(parcellation, {})
        for trials,tdict in pdict.items():
            for condition,cdict in tdict.items():

                for feature, data in cdict.items():
                    feats[parcellation][feature] = feats[parcellation].get(feature, {})
                    feats[parcellation][feature][condition] = feats[parcellation][feature].get(condition, {})

                    #print(feature)
                    #print(condition)
                    #print(session)
                    #print(data.shape)

                    #if len(data) > 0:
                    #    if "All1" in feats[parcellation][feature][condition]:
                    #        feats[parcellation][feature][condition]["All1"] = np.append(feats[parcellation][feature][condition]["All1"],data,axis=0)
                    #    else:
                    #        feats[parcellation][feature][condition]["All1"] = data #[:,0,:  ,:]

                    feats[parcellation][feature][condition][session]= data #[:,0,:,:]
                    

print_dict_keys(feats)


mean
leftResponse_leftStim
GN06.2021-03-26_10-53-05
(115, 8)
autocovariance_timelags~[1]
leftResponse_leftStim
GN06.2021-03-26_10-53-05
(115, 1, 8, 8)
mean
leftResponse_rightStim
GN06.2021-03-26_10-53-05
(17, 8)
autocovariance_timelags~[1]
leftResponse_rightStim
GN06.2021-03-26_10-53-05
(17, 1, 8, 8)
mean
rightResponse_rightStim
GN06.2021-03-26_10-53-05
(125, 8)
autocovariance_timelags~[1]
rightResponse_rightStim
GN06.2021-03-26_10-53-05
(125, 1, 8, 8)
mean
rightResponse_leftStim
GN06.2021-03-26_10-53-05
(23, 8)
autocovariance_timelags~[1]
rightResponse_leftStim
GN06.2021-03-26_10-53-05
(23, 1, 8, 8)
mean
noResponse
GN06.2021-03-26_10-53-05
(10, 8)
autocovariance_timelags~[1]
noResponse
GN06.2021-03-26_10-53-05
(10, 1, 8, 8)
mean
leftResponse_leftStim
GN06.2021-03-26_10-53-05
(115, 64)
autocovariance_timelags~[1]
leftResponse_leftStim
GN06.2021-03-26_10-53-05
(115, 1, 64, 64)
mean
leftResponse_rightStim
GN06.2021-03-26_10-53-05
(17, 64)
autocovariance_timelags~[1]
leftResponse_rightSti

### Saving

In [70]:
configuration_name = "Choice_Decoder_GN06_Delay_EC.FC_All_fixed" #"Stimulus_Decoder_GN06_FC.EC" #
output_path = Path.cwd()/f"results/{configuration_name}"

if not os.path.exists(output_path):
   os.makedirs(output_path)

np.save(Path(output_path)/f"feats_transformed.npy", feats)

## Visualization

### Load Parcellations to get labels

In [71]:
#Get arbitrary session (TODO uses dict before formatting, preferably everything is based on new dict so we just need to load that one)
example_session = Path(list((feat_dict.keys()))[0]) 

#Get list of parcellations and features
parcellations = list(feats.keys())
features = list(next(iter(feats.values())).keys())

labels = {}
for parcellation_name in list(feats.keys()):

    #Load parcellation from first session to get labels
    res_path = Path(path.abspath('')) /'results'
    parcellation_path = Path(res_path/example_session/Path(parcellation_name)/"data.h5")
    parcellation = DecompData.load(parcellation_path)

    labels[parcellation_name] = parcellation.spatial_labels


print(labels)

#Ignore that hashes do not match, I'll remove that as hashes of dicts/objects are just not deterministic

df hashes do not match
df hashes do not match


{"anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,MOs-L,SSp-bfd-L,VISrl-L,VISp-L']": array(['VISpᴿ   ', 'VISrlᴿ  ', 'SSp-bfdᴿ', 'MOsᴿ    ', 'MOsᴸ    ',
       'SSp-bfdᴸ', 'VISrlᴸ  ', 'VISpᴸ   '], dtype='<U8'), 'anatomical_ROI~[]': array(['FRPᴿ    ', 'MOpᴿ    ', 'MOsᴿ    ', 'SSp-nᴿ  ', 'SSp-bfdᴿ',
       'SSp-llᴿ ', 'SSp-mᴿ  ', 'SSp-ulᴿ ', 'SSp-trᴿ ', 'SSp-unᴿ ',
       'SSsᴿ    ', 'AUDdᴿ   ', 'AUDpᴿ   ', 'AUDpoᴿ  ', 'AUDvᴿ   ',
       'VISalᴿ  ', 'VISamᴿ  ', 'VISlᴿ   ', 'VISpᴿ   ', 'VISplᴿ  ',
       'VISpmᴿ  ', 'VISliᴿ  ', 'VISporᴿ ', 'ACAdᴿ   ', 'PLᴿ     ',
       'RSPaglᴿ ', 'RSPdᴿ   ', 'RSPvᴿ   ', 'VISaᴿ   ', 'VISrlᴿ  ',
       'TEaᴿ    ', 'MOBᴿ    ', 'MOBᴸ    ', 'TEaᴸ    ', 'VISrlᴸ  ',
       'VISaᴸ   ', 'RSPvᴸ   ', 'RSPdᴸ   ', 'RSPaglᴸ ', 'PLᴸ     ',
       'ACAdᴸ   ', 'VISporᴸ ', 'VISliᴸ  ', 'VISpmᴸ  ', 'VISplᴸ  ',
       'VISpᴸ   ', 'VISlᴸ   ', 'VISamᴸ  ', 'VISalᴸ  ', 'AUDvᴸ   ',
       'AUDpoᴸ  ', 'AUDpᴸ   ', 'AUDdᴸ   ', 'SSsᴸ    ', 'SSp-unᴸ ',
       'SSp-trᴸ ', 'SSp-ulᴸ ', '

### Selecting

In [72]:
#Choose parcellation & feature to visualize
#parcellation = "anatomical_ROI~[]" #'VISp-R,VISrl-R,SSp-bfd-R,MOs-R,MOs-L,SSp-bfd-L,VISrl-L,VISp-L']" #[]" #
#feature = "autocovariance_timelags~[1]" #"moup_timelags~1" #"autocovariance_timelags~[1]"



no_self_connect = False #True

In [82]:
#Now select the features you want to use
def feat_to_df(parcellation,feature):
   keys, means, df, number_trials = [],[],[],[]
   maxi , mini = 0, 0
  
   for key , cond in feats[parcellation][feature].items():
      keys.append(key)
      print(key)

      mean = np.mean(np.squeeze(cond['All']), axis=0)

      #Exclude self-connectness for moup for visualization
      if "moup" in feature:
         np.fill_diagonal(mean,0)

      means.append(mean)
   
      n_trials, *_ = np.squeeze(cond['All']).shape
      number_trials.append(n_trials)

      print("Trials x (Feature):", end=" ")
      print(np.squeeze(cond['All']).shape)
      
      #Append as dataframe
      df.append(pd.DataFrame(means[-1],labels[parcellation],labels[parcellation]))

      #Define min, max over all conditions for axis
      mini = np.min([np.min(means[-1]), mini])
      maxi = np.max([np.max(means[-1]), maxi])
   return keys, means, df, number_trials, parcellation, feature, mini, maxi


### Visualizing

In [74]:
def df_to_plotly(df):
    return {'z': df.values.tolist(),
            'x': df.columns.tolist(),
            'y': df.index.tolist()}

def diff(x,y):
    #np.std([x,y]]
    return np.abs(y -x)

def plot_matrix_diff_2D(keys, means, df, number_trials, parcellation, feature, mini, maxi,fc_or_ec):
    offset = 1 # Cause subplots start at index 1?
    col_row_n = 1+len(df)
    types = [[{"type": "table"}]] + [[{"type": "heatmap"}]]*(col_row_n**2 - 1)
    types = np.reshape(types, (col_row_n,col_row_n)).tolist()

    fig = make_subplots(rows=col_row_n, cols=col_row_n, shared_xaxes=True, shared_yaxes=True, column_titles = [""] + keys, row_titles = [""] +  keys , column_widths = [500]*(col_row_n) , row_heights = [500]*(col_row_n),
                        specs=types, horizontal_spacing =0.02, vertical_spacing=0.02)


    for i in range(offset,offset+col_row_n):
        

        for j in range(offset,offset+col_row_n):
            if i == 1 and j==1:
                fig.add_trace( go.Table(columnwidth = [120,60],header=dict(values=['Condition', '#Trials']),
                                cells=dict(values=[keys, number_trials])), row=i, col= j)
                fig.data[-1].name = f"Number of trials"
                fig.update_traces(domain=dict(x=[0, 0.12]))
            elif i == 1:
                fig.add_trace( go.Heatmap(df_to_plotly(df[j-2]), colorscale= 'viridis', zauto=False, zmin= mini, zmax= maxi), row=i, col= j)
                fig.data[-1].name = f"μ({keys[j-2]})"

                #w , h = df[i].shape
                #fig.add_hline(y=h/2-0.5, line_dash="dash", line_color="white")
                #fig.add_vline(x=w/2-0.5, line_dash="dash", line_color="white")
            elif j == 1:
                fig.add_trace( go.Heatmap(df_to_plotly(df[i-2]), colorscale= 'viridis', zauto=False, zmin= mini, zmax= maxi), row= i, col= j)
                fig.data[-1].name = f"μ({keys[i-2]})"
            else:
                std = pd.DataFrame( diff(means[i-2],means[j-2]) ,labels[parcellation],labels[parcellation])
                fig.add_trace( go.Heatmap(df_to_plotly(std), colorscale= 'viridis', zauto=False, zmin= mini, zmax= maxi), row= i, col= j)
                fig.data[-1].name = f"|μ({keys[i-2]})<br>-μ({keys[j-2]})|"

            
    fig.update_xaxes(tickmode='linear', matches='x')
    fig.update_yaxes(tickmode='linear',autorange="reversed", matches='y')

    fig.update_layout(
        hoverlabel_namelength=-1,
        width=1500,
        height=1500,
            title=dict( 
            text=f'Mean {fc_or_ec} Brain Connectivities and their Differences <br><span style="font-size: 14px;">(Given by "{feature}" for "{parcellation}")</span>',
            x=0.5,
            y=0.985,
            font=dict(
                family="Arial",
                size=22,
                color='#000000'
            )
        ))

    fig.show()
    figures_path =output_path/f"{parcellation}_{feature}"
    fig.write_html(f"{figures_path}_{configuration_name}.html")


In [83]:
for p in parcellations:
    for f in features:     
        if "cov" in f:
            plot_matrix_diff_2D(*feat_to_df(p,f),"Functional")
        if "moup" in f:
            plot_matrix_diff_2D(*feat_to_df(p,f),"Effective")



leftResponse_leftStim
Trials x (Feature): (1722, 8, 8)
leftResponse_rightStim
Trials x (Feature): (364, 8, 8)
rightResponse_rightStim
Trials x (Feature): (1676, 8, 8)
rightResponse_leftStim
Trials x (Feature): (542, 8, 8)
noResponse
Trials x (Feature): (110, 8, 8)


leftResponse_leftStim
Trials x (Feature): (1722, 64, 64)
leftResponse_rightStim
Trials x (Feature): (364, 64, 64)
rightResponse_rightStim
Trials x (Feature): (1676, 64, 64)
rightResponse_leftStim
Trials x (Feature): (542, 64, 64)
noResponse
Trials x (Feature): (110, 64, 64)


In [76]:
n_comps = 8
edges = list(range(int(n_comps*(n_comps+1)/2))) #range(row*n_comps,(row+1)*n_comps))

resl_path = Path(path.abspath('')) /'results'
#svd_path = Path(resl_path/"GN06_2021-03-26_10-53-05/anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,VISp-L,VISrl-L,SSp-bfd-L,MOs-L']/data.h5")
svd_path = Path(resl_path/"GN06_2021-03-26_10-53-05/anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,VISp-L,VISrl-L,SSp-bfd-L,MOs-L']/data.h5")

parcellation = DecompData.load(svd_path)
print(parcellation.spatial_labels)

#feat_path= Path(resl_path/"GN06_2021-03-26_10-53-05/anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,VISp-L,VISrl-L,SSp-bfd-L,MOs-L']/All/Features/tactile/autocovariance_timelags~[1]/features.h5")
feat_path= Path(resl_path/"GN06_2021-03-26_10-53-05/anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,VISp-L,VISrl-L,SSp-bfd-L,MOs-L']/All/Features/tactile/autocovariance_timelags~[1]/features.h5")

feat = Moup.load(feat_path)
print(feat.feature.shape)

feat_val = np.mean(feat.feature[0,:,:,:],axis=0).flatten()

cutted_labels=parcellation.spatial_labels[:n_comps] if parcellation.spatial_labels is not None else None

#max=0.02
#feat_val = np.clip(feat_val,a_min=0,a_max=max)
#feat_val = feat_val / max
feat_val =  feat_val / np.max(feat_val)
np.set_printoptions(suppress = True)
print(np.asarray(feat_val))

#feat_padded = np.zeros((n_comps,n_comps))
#feat_padded[list_best_feat]=feat_val


print("feat_val")
#print(feat_padded)
#rfe_graph = construct_network(edges, n_nodes = n_comps, feat_type = Feature_Type.UNDIRECTED, edge_weight=None)# 0.01+ 99*feat_val/100)
#nx.set_edge_attributes(rfe_graph, edge_attrs, "edge_color")

print("new f")
rfe_graph_2 = construct_network_from_feat(edges, n_comps, feat_type = Feature_Type.UNDIRECTED, feat_val = visualized_data)

rfe_graph = add_bokeh_attributes(rfe_graph_2)
print(rfe_graph)
print(rfe_graph_2)
print(rfe_graph_2.nodes[0])


plot_glassbrain_bokeh(graph=rfe_graph,components_spatials=parcellation.spatials,components_labels=cutted_labels,save_path=resl_path/"glassbrain.html",small_file=True)

df hashes do not match


['VISpᴿ   ' 'VISrlᴿ  ' 'SSp-bfdᴿ' 'MOsᴿ    ' 'VISpᴸ   ' 'VISrlᴸ  '
 'SSp-bfdᴸ' 'MOsᴸ    ']
(83, 1, 8, 8)
[ 1.          0.92138093  0.4731039  -0.12937607  0.5934896   0.40746371
  0.21237785 -0.21870691  0.9148822   0.92178956  0.57632586 -0.02766459
  0.57160778  0.38459458  0.13463471 -0.1432456   0.53520428  0.598699
  0.59686611  0.10489918  0.36664011  0.28926158  0.0078214  -0.03144929
  0.2772671   0.41408207  0.46519106  0.22874269  0.35261272  0.40419935
  0.32935626  0.23759095  0.53981846  0.5257944   0.27188268 -0.07801433
  0.43466365  0.34585644  0.20873406 -0.06338716  0.41260523  0.38548618
  0.18137889 -0.01984158  0.42290614  0.40112128  0.3150107   0.05690445
  0.51313449  0.41552412  0.06872742  0.10194327  0.52538524  0.55794873
  0.89369209  0.35078956  0.24362551  0.36332204  0.35144807  0.29727521
  0.41840596  0.50006407  0.55078878  0.42242586]
feat_val
new f


NameError: name 'visualized_data' is not defined

In [ ]:
from dash import Dash, dcc, html, Input, Output
import plotly.express as px

app = Dash(__name__)


app.layout = html.Div([
    html.H4('Olympic medals won by countries'),
    dcc.Graph(id="graph"),
    html.P("Medals included:"),
    dcc.Checklist(
        id='medals',
        options=["gold", "silver", "bronze"],
        value=["gold", "silver"],
    ),
])


@app.callback(
    Output("graph", "figure"), 
    Input("medals", "value"))
def filter_heatmap(cols):
    df = px.data.medals_wide(indexed=True) # replace with your own data source
    fig = px.imshow(df[cols])
    return fig


app.run_server(debug=True, use_reloader=False)

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

Dash is running on http://127.0.0.1:8050/

 * Serving Flask app '__main__'
 * Debug mode: on
